## Missing: 

- Boundary condition for dust particle! 
     - start with a square, work up if time allows

In [2]:
import math
import numpy as np
import scipy as sp
from matplotlib import pyplot as plt 
import sys, os 
import time
import csv
%matplotlib inline

### Inputs 

Types: 
    - Constants
        - EPS0
        - QE
        - K 
        - AMU
        - MI
        
    - Simulation inputs
    - Plasma parameters 
    - Domain parameters 
    - Specific weight 
    - Particle arrays 
        - Position 
        - Velocity 

In [2]:
# constants 
EPS0 = 8.85 * 10 ** -12
QE = 1.602 * 10 ** -19 
K = 1.381 * 10 ** -23 
AMU = 1.661 * 10 ** -27
MI = 40 * AMU #mass of an Ar+ ion 

#simulation inputs 
N = 20000 #max particles 
n0 = 1 * 10 ** 12 #density 
V_ref = 0 #reference potential 
Te = 1  #electron temperature in eV 
Ti = 0.1 #ion temperature in eV
V_d = -5.1 #dust potential (use values from lit)
v_drift = 7000
tol = 1 * 10 ** -4
iterations = 200


#plasma parameters 
lambd_D = np.sqrt( EPS0 * Te /(n0 * QE) ) #NOTE: update this variable, currently ~0.007  
vth = np.sqrt((2 * QE * Ti) / MI) # ~2195
v0 = 0.2 #stream velocity 
#print(lambd_D, vth)

#domain parameters 
nx = 10
ny = 10
J = nx * ny 
dx = dy = dh = lambd_D
Lx = nx * dx 
Ly = ny * dy 
dt = (0.1 * dx) / v_drift 
np_in = (ny-1) * 15 # adds 135 particles per time step 
print(Lx, lambd_D)

#specific weight 
flux = n0 * v_drift * Ly 
npt = flux * dt #particles created per timestep 
sw = npt / np_in #specific weight 
q_mp = 1 #macroparticle charge 

# particle arrays
p_pos = np.zeros([N,2])
p_velo = np.zeros([N,2])


0.0743259347017 0.00743259347017


### Stencil matrix for potential solver 

In [3]:
start = time.clock() # Keeping track of computational time 

#stencil array used in potential solver 

def stencil_fd(J, dx, dh, nx, ny):
    """Uses the finite difference scheme"""
    #E = []
    
    #source = rho
    M = np.zeros((J,J))
    
    for i in range (1, nx-1):
        for j in range(1, ny-1): 
            u = (j-1) * nx + i
            M[u, u] = -4. / (dh * dh) 
            M[u, u-1] = 1. / (dh * dh)
            M[u, u+1] = 1. / (dh * dh)
            M[u, u-nx] = 1. / (dh * dh)
            M[u, u+ (nx-2)] = 1. / (dh * dh)    
    
    for i in range (0, nx):
        u = i+1
        M[u,u] = -1. / dh
        M[u,u+nx] = 1. / dh 
        
    for i in range (0,nx): 
        u = (ny-1) * nx  + i 
        M[u, u-nx] = 1. / dh
        M[u, u] = -1. / dh 
        
    for j in range (0, ny): 
        u = (j-1) * nx + nx 
        M[u, :] = np.zeros([1, J])
        M[u, u-1] = 1. / dh 
        M[u, u] = -1. / dh 
        
    for j in range(0, ny): 
        u = (j-1) * nx + 1 
        M[u, :] = np.zeros([1, J])
        M[u, u] = 1.     
        
    return M

print("Clocking in at %s seconds"  % (time.clock() - start))

Clocking in at 0.0009500000000000064 seconds


### 2D potential solver using Gauss-Seidel method

5.21.2018

There are appears to be operational issues with this solver. It may have something to do with the fact that python, unlike matlab does not do matrix operations. Need to find a way through this.

In [3]:
start = time.clock() # Keeping track of computational time 

def solver_2d(rho, tol, Ti, n0, V, QE): 
    'Uses Gauss Sidel method'

    iter = 200

    M = stencil_fd(J, dx, dh, nx, ny)
    
    source = rho
    NX = np.size(source,0)
    NY = np.size(source,1)
    NN = np.size(source)
    
    b0 = np.reshape(source, (NN,1))
    x = np.reshape(V, (np.size(V), 1))
    
    #print(np.size(x), np.size(b0), np.size(M)) 100 100 1000 as of 5/21
    
    for count in range (0, iter):

        #boltzmann relation for electrons (fluid)
        b = b0 - n0 * np.exp((x - V_ref)/ Te)
        #initial values: n0 = 1E12, b0 = zeros(NN,1), x = zeros(v, 1)
        
        b = (b * QE) / EPS0
        #print(b) <-- this takes a looooong time to print. 
        #the x[i] below feeds back into b and things start to go haywire real quick
    
        b[0:NX-1] = 0 
        b[NN-NX+1 : NN] = 0 
        b[NX: NX : NN] = 0 
        b[1:NX:NN] = V_ref
        
        for i in range (0, NN):
            # x[i] appears to be the culprit...the source of the nans.
            x[i] = (b[i] -  ( np.dot(M[i, 0:i], x[0: i]) -  np.dot(M[i, i+1 : NN-1] , x[i+1:NN-1] ) ) ) / (M[i,i])
            V = np.reshape(x, (NX,NY))
        
        if count%10 == 0 or count == iter:            
            R = np.linalg.norm(b - (M*x)) 
            if R <= tol:
                print('Solver converged.')
                break
        
        if R > tol: 
            print('Solver failed to converge. Check R!')
        
    return V
print("Clocking in at %s seconds"  % (time.clock() - start))

Clocking in at 0.0005919999999997039 seconds


### Main Cycle

Calling above functions.

- Solves E field 
- Generates and distributes new particles 
- Moves particles 
- Add/removes particles at boundaries (not yet implemented) 

Notes: 5.21.2018

Plot works, and particles are randomly scattered in each time step. However it does not appear that any appreciable number of particles are being generated (I dont notice a difference between plots). May have have to do with the fact that the solver technically doesn't work...

In [ ]:
start = time.clock()

NP = 0
V = np.ones((ny,nx)) * V_ref

print('Calculating...')

for count in range(0, iterations):
    q = np.zeros((nx, ny))
    rho = np.zeros((ny, nx))
    Ex = np.zeros([nx, ny])
    Ey = np.zeros([nx, ny])
     
    for p in range (1, NP):  
        fi = (1 + p_pos[p,0]) / (dh) 
        i = np.floor(fi) # <-- problem may arise here??
        hx = fi - i  
        #print(hx) => wont print   
        
        fj = (1 + p_pos[p,1]) / (dh)
        j = np.floor(fj)
        hy = fj - j 
        #print(hy) => wont print
        
        q[i,j] = q[i,j] + (1-(hx)) * (1-(hy))
        q[i+1, j] = q[i+1, j] + (hx) * (1-(hy))
        q[i, j+1] = q[i, j+1] + (1-(hx)) * (hx) 
        q[i+1, j+1] = q[i+1, j+1] + (hx) * (hx) 

    rho = (sw + q_mp * q) / (dh * dh)
       
    rho[0,:] = 2 * rho[0,:]
    rho[-1, :] = 2 * rho[-1, :]
    rho[:, 0] = 2 * rho[:, 0]
    rho[:, -1] = 2 * rho[:, -1]
    
    rho = rho + (1 * 10 ** 4)
    #print(rho)

    #calling potential solver 
    V = solver_2d(rho, tol, Ti, n0, V, QE)
    #print(V) #START HERE!!! => nan Check solver_2d 
    
    #E field solver
    
    E = np.zeros([nx, ny])
    #internal nodes 
    Ex[1:nx-1, :] = V[0:nx-2,:] - V[nx-(nx-2):, :]
    Ey[0: ,1:nx-1] = V[:, 0:ny-2] - V[:, 2:ny]

    #boundaries
    #multiplied by 2 to keep values equivalent to internal nodes
    Ex[0,:] = 2* (V[0,:] - V[1,:]) 
    Ex[nx-1, :] = 2 * (V[nx-2,:] - V[nx-1, :])
    
    Ey[:, 0] = 2 * (V[:,0] - V[:,1])
    Ey[:,ny-1] = 2 * (V[:, ny-2] - V[:, ny-1])
    
    Ex = np.floor (Ex / (2 * dx))                                       
    Ey = Ey / (2 * dy)
    
    #generate particles 
    
    if NP + np_in >= N:
        np_in = N - NP
   
    #insert paritcles 
    
    p_pos[NP:NP+np_in, 1:] = np.random.rand(np_in,1) * dh #x position 
    p_pos[NP:NP+np_in, 1:] = np.random.rand(np_in,1) * Ly #y position 
    
    #sample Maxwellian in x,y 
    #add drift velocity in x 
    
    p_velo[NP:NP+np_in, 1:] = v_drift + (-1.5 + np.random.rand(np_in,1) + np.random.rand(np_in,1) 
                                         + np.random.rand(np_in, 1)) * vth 
    p_velo[NP:NP+np_in, 2:] = 0.5 * (-1.5 + np.random.rand(np_in,1) + np.random.rand(np_in,1) 
                                     + np.random.rand(np_in, 1)) * vth
    
    #move particles 
    p = 1 
    
    while p <= NP:
            
        fi = 1 + p_pos[p,0]/dx 
        i = np.floor(fi)
        hx = fi - i  
                
        fj = 1+ p_pos[p,1]/dy 
        j = np.floor(fj)
        hy = fj - j 
        
        E = ([Ex[i, j], Ey[i,j]]) * (1-int(hx)) * (1-(hy))                                                
        E = E + ([Ex[i + 1, j], Ey[i + 1, j]]) * (hx) * (1-(hy))                                                
        E = E + ([Ex[i, j + 1], Ey[i + 1, j]]) * (1-(hx)) * (hy)                                                
        E = E + ([Ex[i + 1, j + 1], Ey[i + 1, j + 1]]) * (hx) * (hy)  
        
        F = QE * E 
        a = F/MI 
        
        p_pos[p, :] = p_velo[p, :] + a * dt 
        p_velo[p, :] = p_pos[p, :] + p_velo[p, :] * dt 
        
        if p_pos[p,1] < 0: 
            p_pos[p,1] = -p_pos[p,1]
            p_velo[p,1] = -p_velo[p,1]
            
        p = p + 1 
        
    #print(E) E's are all 0...
    #print(V) V's are all nan...
    print(V)
#    if count%10 == 0 or count == iterations:
#        fig = plt.figure(1, figsize=(8.0,6.0))
#        plt.plot(p_pos, p_velo,'m.', ms=3)
#        #plt.title('Two-Stream Instability', fontsize = 16, fontweight = 'bold', color = 'w')
#        #plt.xticks([0, L], color = 'k', fontsize = 18)  # color = 'w'
#        plt.xlabel('x', fontsize = 18 , color = 'k')
#        #plt.yticks([-2*v0, -v0, 0, v0, 2*v0], color = 'k', fontsize = 18)
#        plt.ylabel('v', fontsize = 18, rotation=0 , color = 'k')
#        #plt.savefig('pngs/20180428/Run3_pngs_20180428/Frame_{count}.png'. format(count=count), frameon= True, transparent=True) #facecolor = 'k',
#        plt.show()
#        #plt.close()
   
print("Clocking in at %s seconds"  % (time.clock() - start))

Calculating...
[[-17565.34821823]
 [-17833.52147623]
 [-17833.52147623]
 [-17833.52147623]
 [-17833.52147623]
 [-17833.52147623]
 [-17833.52147623]
 [-17833.52147623]
 [-17833.52147623]
 [-17565.34821823]
 [-17833.52147623]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17833.52147623]
 [-17833.52147623]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17833.52147623]
 [-17833.52147623]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17833.52147623]
 [-17833.52147623]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17967.60810524]
 [-17833.52147623]
 [-17833.52147623]
 [-17967.6081052

/Users/Isabel/anaconda/lib/python3.5/site-packages/ipykernel/__main__.py:34: RuntimeWarning: divide by zero encountered in true_divide
/Users/Isabel/anaconda/lib/python3.5/site-packages/ipykernel/__main__.py:38: RuntimeWarning: invalid value encountered in multiply


[[ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]]
[[ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]
 [ nan]

### References 

1. https://www.particleincell.com/2010/es-pic-method/#charge_density
2. 

### Misc. 